## Data Dictionary

Below is a detailed description of each feature in both tables included in the Credit Card Approval Prediction dataset:

### application_record.csv

| Feature Name         | Explanation                | Remarks                                                                                           |
|----------------------|---------------------------|---------------------------------------------------------------------------------------------------|
| ID                   | Client number             | Unique identifier for each client                                                                  |
| CODE_GENDER          | Gender                    | Values: M (male), F (female)                                                                      |
| FLAG_OWN_CAR         | Is there a car            | 1 if the client owns a car, 0 otherwise                                                           |
| FLAG_OWN_REALTY      | Is there a property       | 1 if the client owns property, 0 otherwise                                                        |
| CNT_CHILDREN         | Number of children        | Number of children the client has                                                                  |
| AMT_INCOME_TOTAL     | Annual income             | Client's annual income                                                                            |
| NAME_INCOME_TYPE     | Income category           | Type of income: e.g., Working, Commercial associate, Pensioner, State servant, Unemployed         |
| NAME_EDUCATION_TYPE  | Education level           | Level of education: e.g., Higher education, Secondary, Academic degree, Lower secondary           |
| NAME_FAMILY_STATUS   | Marital status            | Client's family status: e.g., Single, Married, Civil marriage, Separated, Widow                   |
| NAME_HOUSING_TYPE    | Way of living             | Type of housing: e.g., Own house/apartment, With parents, Municipal, Co-op, Rented, Office apt    |
| DAYS_BIRTH           | Birthday                  | Counted backwards from current day (0); negative values, -1 means yesterday                       |
| DAYS_EMPLOYED        | Start date of employment  | Counted backwards from current day (0). If positive, client is currently unemployed               |
| FLAG_MOBIL           | Is there a mobile phone   | 1 if the client has a mobile phone, 0 otherwise                                                   |
| FLAG_WORK_PHONE      | Is there a work phone     | 1 if the client has a work phone, 0 otherwise                                                     |
| FLAG_PHONE           | Is there a phone          | 1 if the client has a phone, 0 otherwise                                                          |
| FLAG_EMAIL           | Is there an email         | 1 if the client has an email address, 0 otherwise                                                 |
| OCCUPATION_TYPE      | Occupation                | Client's occupation                                                                               |
| CNT_FAM_MEMBERS      | Family size               | Number of family members                                                                          |

### credit_record.csv

| Feature Name    | Explanation              | Remarks                                                                                                                                                                                      |
|-----------------|-------------------------|----------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------|
| ID              | Client number           | Unique identifier for each client                                                                                                                      |
| MONTHS_BALANCE  | Record month            | The month of the extracted data is the starting point; 0 is the current month, -1 is the previous month, and so on                                    |
| STATUS          | Status                  | Payment status: <br>0 = 1–29 days past due <br>1 = 30–59 days past due <br>2 = 60–89 days overdue <br>3 = 90–119 days overdue <br>4 = 120–149 days overdue <br>5 = Overdue or bad debts, write-offs for more than 150 days <br>C = Paid off that month <br>X = No loan for the month |

---

This data dictionary provides clarity on the attributes available for modeling and feature engineering in the credit approval prediction task.


In [0]:
%pip install xgboost lightgbm catboost  --quiet

Note: you may need to restart the kernel using %restart_python or dbutils.library.restartPython() to use updated packages.


In [0]:
import warnings
warnings.filterwarnings('ignore')
import pandas as pd
import numpy as np
import pandas as pd   
import matplotlib.pyplot as plt
import seaborn as sns

from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score, confusion_matrix
from sklearn.linear_model import LogisticRegression
from sklearn.tree import DecisionTreeClassifier
from sklearn import svm
from sklearn.ensemble import RandomForestClassifier

from xgboost import XGBClassifier
from lightgbm import LGBMClassifier
from catboost import CatBoostClassifier

In [0]:
record = pd.read_csv("Data/credit_record.csv")
display(record.head())

ID MONTHS_BALANCE STATUS 5001711 0 X 5001711 -1 0 5001711 -2 0 5001711 -3 0 5001712 0 C

In [0]:
data = pd.read_csv("Data/application_record.csv")
data.head()

ID CODE_GENDER  ... OCCUPATION_TYPE CNT_FAM_MEMBERS
0  5008804           M  ...             NaN             2.0
1  5008805           M  ...             NaN             2.0
2  5008806           M  ...  Security staff             2.0
3  5008808           F  ...     Sales staff             1.0
4  5008809           F  ...     Sales staff             1.0

[5 rows x 18 columns]

In [0]:
record.isnull().sum()

ID                0
MONTHS_BALANCE    0
STATUS            0
dtype: int64

In [0]:
for col in record.columns:
    print(f"\n Column: {col}")
    print(record[col].unique())


 Column: ID
[5001711 5001712 5001713 ... 5150484 5150485 5150487]

 Column: MONTHS_BALANCE
[  0  -1  -2  -3  -4  -5  -6  -7  -8  -9 -10 -11 -12 -13 -14 -15 -16 -17
 -18 -19 -20 -21 -22 -23 -24 -25 -26 -27 -28 -29 -30 -31 -32 -33 -34 -35
 -36 -37 -38 -39 -40 -41 -42 -43 -44 -45 -46 -47 -48 -49 -50 -51 -52 -53
 -54 -55 -56 -57 -58 -59 -60]

 Column: STATUS
['X' '0' 'C' '1' '2' '3' '4' '5']


### credit_record.csv

| Feature Name    | Explanation              | Remarks                                                                                                                                                                                      |
|-----------------|-------------------------|----------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------|
| ID              | Client number           | Unique identifier for each client                                                                                                                      |
| MONTHS_BALANCE  | Record month            | The month of the extracted data is the starting point; 0 is the current month, -1 is the previous month, and so on                                    |
| STATUS          | Status                  | Payment status: <br>0 = 1–29 days past due <br>1 = 30–59 days past due <br>2 = 60–89 days overdue <br>3 = 90–119 days overdue <br>4 = 120–149 days overdue <br>5 = Overdue or bad debts, write-offs for more than 150 days <br>C = Paid off that month <br>X = No loan for the month |

---

In [0]:
begin_month = (
    record.groupby("ID")['MONTHS_BALANCE']
    .min()
    .rename("begin_month")
    .to_frame()
)
begin_month.head()

begin_month
ID                  
5001711           -3
5001712          -18
5001713          -21
5001714          -14
5001715          -59

In [0]:

record['dep_value'] = None
record.loc[record['STATUS'].isin(['2', '3', '4', '5']), 'dep_value'] = 'Yes'

cpunt = record.groupby('ID')['dep_value'].apply(lambda x: 'Yes' if (x == 'Yes').any() else 'No')
cpunt = cpunt.to_frame()


In [0]:
print(cpunt['dep_value'].value_counts())
cpunt['dep_value'].value_counts(normalize=True)

No     45318
Yes      667
Name: dep_value, dtype: int64


No     0.985495
Yes    0.014505
Name: dep_value, dtype: float64

In [0]:
data = pd.merge(data, begin_month, how = "left", on = "ID")
data = pd.merge(data, cpunt, how = "inner", on = "ID" )
data['label'] = data['dep_value'].map({'Yes': 1, 'No': 0})
display(data)

ID CODE_GENDER FLAG_OWN_CAR FLAG_OWN_REALTY CNT_CHILDREN AMT_INCOME_TOTAL NAME_INCOME_TYPE NAME_EDUCATION_TYPE NAME_FAMILY_STATUS NAME_HOUSING_TYPE DAYS_BIRTH DAYS_EMPLOYED FLAG_MOBIL FLAG_WORK_PHONE FLAG_PHONE FLAG_EMAIL OCCUPATION_TYPE CNT_FAM_MEMBERS begin_month dep_value label 5008804 M Y Y 0 427500.0 Working Higher education Civil marriage Rented apartment -12005 -4542 1 1 0 0 null 2.0 -15.0 No 0 5008805 M Y Y 0 427500.0 Working Higher education Civil marriage Rented apartment -12005 -4542 1 1 0 0 null 2.0 -14.0 No 0 5008806 M Y Y 0 112500.0 Working Secondary / secondary special Married House / apartment -21474 -1134 1 0 0 0 Security staff 2.0 -29.0 No 0 5008808 F N Y 0 270000.0 Commercial associate Secondary / secondary special Single / not married House / apartment -19110 -3051 1 0 1 1 Sales staff 1.0 -4.0 No 0 5008809 F N Y 0 270000.0 Commercial associate Secondary / secondary special Single / not married House / apartment -19110 -3051 1 0 1 1 Sales staff 1.0 -26.0 No 0 5008810 F N Y 0 270000.0 Commercial associate Secondary / secondary special Single / not married House / apartment -19110 -3051 1 0 1 1 Sales staff 1.0 -26.0 No 0 5008811 F N Y 0 270000.0 Commercial associate Secondary / secondary special Single / not married House / apartment -19110 -3051 1 0 1 1 Sales staff 1.0 -38.0 No 0 5008812 F N Y 0 283500.0 Pensioner Higher education Separated House / apartment -22464 365243 1 0 0 0 null 1.0 -20.0 No 0 5008813 F N Y 0 283500.0 Pensioner Higher education Separated House / apartment -22464 365243 1 0 0 0 null 1.0 -16.0 No 0 5008814 F N Y 0 283500.0 Pensioner Higher education Separated House / apartment -22464 365243 1 0 0 0 null 1.0 -17.0 No 0 5008815 M Y Y 0 270000.0 Working Higher education Married House / apartment -16872 -769 1 1 1 1 Accountants 2.0 -5.0 No 0 5112956 M Y Y 0 270000.0 Working Higher education Married House / apartment -16872 -769 1 1 1 1 Accountants 2.0 -42.0 No 0 5008819 M Y Y 0 135000.0 Commercial associate Secondary / secondary special Married House / apartment -17778 -1194 1 0 0 0 Laborers 2.0 -17.0 No 0 5008820 M Y Y 0 135000.0 Commercial associate Secondary / secondary special Married House / apartment -17778 -1194 1 0 0 0 Laborers 2.0 -16.0 No 0 5008821 M Y Y 0 135000.0 Commercial associate Secondary / secondary special Married House / apartment -17778 -1194 1 0 0 0 Laborers 2.0 -8.0 No 0 5008822 M Y Y 0 135000.0 Commercial associate Secondary / secondary special Married House / apartment -17778 -1194 1 0 0 0 Laborers 2.0 -22.0 No 0 5008823 M Y Y 0 135000.0 Commercial associate Secondary / secondary special Married House / apartment -17778 -1194 1 0 0 0 Laborers 2.0 -7.0 No 0 5008824 M Y Y 0 135000.0 Commercial associate Secondary / secondary special Married House / apartment -17778 -1194 1 0 0 0 Laborers 2.0 -3.0 No 0 5008825 F Y N 0 130500.0 Working Incomplete higher Married House / apartment -10669 -1103 1 0 0 0 Accountants 2.0 -25.0 No 0 5008826 F Y N 0 130500.0 Working Incomplete higher Married House / apartment -10669 -1103 1 0 0 0 Accountants 2.0 -30.0 No 0 5008830 F N Y 0 157500.0 Working Secondary / secondary special Married House / apartment -10031 -1469 1 0 1 0 Laborers 2.0 -31.0 No 0 5008831 F N Y 0 157500.0 Working Secondary / secondary special Married House / apartment -10031 -1469 1 0 1 0 Laborers 2.0 -19.0 No 0 5008832 F N Y 0 157500.0 Working Secondary / secondary special Married House / apartment -10031 -1469 1 0 1 0 Laborers 2.0 -34.0 No 0 5008834 F N Y 1 112500.0 Working Secondary / secondary special Single / not married House / apartment -10968 -1620 1 0 0 0 null 2.0 -44.0 No 0 5008835 F N Y 1 112500.0 Working Secondary / secondary special Single / not married House / apartment -10968 -1620 1 0 0 0 null 2.0 -44.0 No 0 5008836 M Y Y 3 270000.0 Working Secondary / secondary special Married House / apartment -12689 -1163 1 0 0 0 Laborers 5.0 -24.0 No 0 5008837 M Y Y 3 270000.0 Working Secondary / secondary special Married House / apartment -12689 -1163 1 0 0 0 Laborers 

In [0]:
data.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 36457 entries, 0 to 36456
Data columns (total 21 columns):
 #   Column               Non-Null Count  Dtype  
---  ------               --------------  -----  
 0   ID                   36457 non-null  int64  
 1   CODE_GENDER          36457 non-null  object 
 2   FLAG_OWN_CAR         36457 non-null  object 
 3   FLAG_OWN_REALTY      36457 non-null  object 
 4   CNT_CHILDREN         36457 non-null  int64  
 5   AMT_INCOME_TOTAL     36457 non-null  float64
 6   NAME_INCOME_TYPE     36457 non-null  object 
 7   NAME_EDUCATION_TYPE  36457 non-null  object 
 8   NAME_FAMILY_STATUS   36457 non-null  object 
 9   NAME_HOUSING_TYPE    36457 non-null  object 
 10  DAYS_BIRTH           36457 non-null  int64  
 11  DAYS_EMPLOYED        36457 non-null  int64  
 12  FLAG_MOBIL           36457 non-null  int64  
 13  FLAG_WORK_PHONE      36457 non-null  int64  
 14  FLAG_PHONE           36457 non-null  int64  
 15  FLAG_EMAIL           36457 non-null 

In [0]:
data = data.rename(columns={'CODE_GENDER':'Gender','FLAG_OWN_CAR':'Car','FLAG_OWN_REALTY':'Reality',
                         'CNT_CHILDREN':'ChldNo','AMT_INCOME_TOTAL':'inc',
                         'NAME_EDUCATION_TYPE':'edutp','NAME_FAMILY_STATUS':'famtp',
                        'NAME_HOUSING_TYPE':'houtp','FLAG_EMAIL':'email',
                         'NAME_INCOME_TYPE':'inctp','FLAG_WORK_PHONE':'wkphone',
                         'FLAG_PHONE':'phone','CNT_FAM_MEMBERS':'famsize',
                        'OCCUPATION_TYPE':'occyp'
                        })

In [0]:
data.isnull().sum()

ID                   0
Gender               0
Car                  0
Reality              0
ChldNo               0
inc                  0
inctp                0
edutp                0
famtp                0
houtp                0
DAYS_BIRTH           0
DAYS_EMPLOYED        0
FLAG_MOBIL           0
wkphone              0
phone                0
email                0
occyp            11323
famsize              0
begin_month          0
dep_value            0
label                0
dtype: int64

Dont forget Change days_employed

In [0]:
data = data.drop(columns = ['occyp', 'dep_value', 'email', 'phone', 'wkphone', 'FLAG_MOBIL'])

In [0]:
data.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 36457 entries, 0 to 36456
Data columns (total 15 columns):
 #   Column         Non-Null Count  Dtype  
---  ------         --------------  -----  
 0   ID             36457 non-null  int64  
 1   Gender         36457 non-null  object 
 2   Car            36457 non-null  object 
 3   Reality        36457 non-null  object 
 4   ChldNo         36457 non-null  int64  
 5   inc            36457 non-null  float64
 6   inctp          36457 non-null  object 
 7   edutp          36457 non-null  object 
 8   famtp          36457 non-null  object 
 9   houtp          36457 non-null  object 
 10  DAYS_BIRTH     36457 non-null  int64  
 11  DAYS_EMPLOYED  36457 non-null  int64  
 12  famsize        36457 non-null  float64
 13  begin_month    36457 non-null  float64
 14  label          36457 non-null  int64  
dtypes: float64(3), int64(5), object(7)
memory usage: 4.5+ MB
